In [4]:
from langchain.embeddings import HuggingFaceBgeEmbeddings

model_norm = HuggingFaceBgeEmbeddings(
    model_name="BAAI/bge-large-en",
    encode_kwargs={'normalize_embeddings': True}
)

In [2]:
from langchain.text_splitter import CharacterTextSplitter
from langchain.vectorstores import FAISS
from langchain.document_loaders import PyPDFLoader
import os

base_path = '../../Library/CloudStorage/Box-Box/DISC_AI Project/Transripts Pilot'
os.listdir(base_path)

['.chroma',
 '.DS_Store',
 '6.3 Effects of Age and Disuse on Skeletal Muscle.pdf',
 '6.9 Precautions and Contraindications for Resistance Exercise.pdf',
 '6.4 Framework for Resistance Training.pdf',
 'd_db',
 '6.1 Principles of Resistance Exercise.pdf',
 '6.7 Case Application of Oddvar-Holten Method.pdf',
 '6.5 Velocity and Mode Resistsance Training Parameters.pdf',
 '6.6 Volume and Intensity of Resistance Exercise.pdf',
 '6.2 Muscle Adaptations to Resistance Exercise.pdf',
 'p_db',
 '~',
 '6.8 Order and Frequency of Resistance Exercise.pdf']

In [7]:
import glob

pdfs = glob.glob(f'{base_path}/*.pdf')
pages = []
for pdf in pdfs:
    loader = PyPDFLoader(pdf)
    pages += loader.load_and_split()

In [16]:
db = FAISS.from_documents(pages, model_norm)

In [17]:
db.similarity_search('What is resistance training?')

[Document(page_content="mechanically. 00:01:24[BLANK_AUDIO] 00:01:29Now, since we have established what the definition is, I would like to say before we do anything else that resists training within the literature is heavily, heavily covered. 00:01:40As a matter of fact, it is so ubiquitous that it's hardly worth mentioning the fact that, yes, there is literature supporting resistance training. 00:01:50As a matter of fact, when I did a very quick search term for resistance training and rehabilitation, I had almost 44,000 hits. 00:01:59So again, when we go through the material associated with resistance training, it's assuming that we all understand that resistance training does have therapeutic benefits. 00:02:12[BLANK_AUDIO] 00:02:14Okay, so let's talk about some of the elements of muscle performance, and they are strength, endurance, and power. 00:02:20The strength of a muscle is the ability of contractile tissue to produce tension and resultant force based on the demands placed on t

In [18]:
db.save_local("pt_example_db")

In [19]:
new_db = FAISS.load_local("pt_example_db", model_norm)

In [20]:
new_db.similarity_search('What is resistance training?')

[Document(page_content="mechanically. 00:01:24[BLANK_AUDIO] 00:01:29Now, since we have established what the definition is, I would like to say before we do anything else that resists training within the literature is heavily, heavily covered. 00:01:40As a matter of fact, it is so ubiquitous that it's hardly worth mentioning the fact that, yes, there is literature supporting resistance training. 00:01:50As a matter of fact, when I did a very quick search term for resistance training and rehabilitation, I had almost 44,000 hits. 00:01:59So again, when we go through the material associated with resistance training, it's assuming that we all understand that resistance training does have therapeutic benefits. 00:02:12[BLANK_AUDIO] 00:02:14Okay, so let's talk about some of the elements of muscle performance, and they are strength, endurance, and power. 00:02:20The strength of a muscle is the ability of contractile tissue to produce tension and resultant force based on the demands placed on t

In [21]:
old = db.similarity_search('What is resistance training?')
new = new_db.similarity_search('What is resistance training?')
old == new # yay!

True

In [20]:
base_path = '../../Library/CloudStorage/Box-Box/DISC_AI Project/Transcripts Primary Care'
os.listdir(base_path)

['Week 8 Primary Care.pdf',
 'Week 3 Primary Care.pdf',
 'Week 7 Primary Care.pdf',
 'Weeks1_through_10.pdf',
 'Week 9 Primary Care.pdf',
 'Week 2 Primary Care.pdf',
 'Week 1 Primary Care.pdf',
 'Weeks1_through_5.pdf',
 'Week 5 Primary Care.pdf',
 'Week 4 Primary Care.pdf',
 'Week 10 Primary Care.pdf']

In [19]:
base_path = '../../Library/CloudStorage/Box-Box/DISC_AI Project/Transcripts Primary Care/Week 1 Primary Care.pdf'
os.path.exists(base_path)

True

In [14]:
import pypdf

read_pdf = pypdf.PdfReader(base_path)

In [51]:
read_pdf.pages[0].extract_text().startswith('1.')

True

In [55]:
import collections
text_dict = collections.defaultdict(str)
pages = read_pdf.pages
for page in pages:
    page_text = page.extract_text()
    if page_text.startswith('1.'):
        curr = page_text[:3]
        text_dict[curr] += page_text
    else:
        text_dict[curr] += page_text

In [57]:
text_dict['1.2']

"1.2  The Low Back and Lower Extremities; Regional Pain Patterns and Associated Disorders00:00:01Lecture 1.2, regional pain patterns and associated diseases and disorders, low back and lower extremities. 00:00:09[BLANK_AUDIO] 00:00:12So the objectives here are to identify 4 forms you might give to a patient with low back pain to provide additional information about that patient's condition. 00:00:23Describe at least two non-musculoskeletal causes of low back pain and under what circumstances you might reevaluate a musculoskeletal cause of labaquine. 00:00:34Describe symptoms which might lead you to include cauda equina in your list of differential diagnoses. 00:00:42Identify five potentially serious conditions which may mimic less serious musculoskeletal conditions in the pelvis, hip, and thigh. 00:00:52And finally, identify five potentially serious conditions which may mimic less serious musculoskeletal conditions in the knee, lower leg, ankle, and foot. 00:01:03[BLANK_AUDIO] 00:01:06

In [78]:
os.makedirs('./data/week_1')

In [79]:
from langchain.text_splitter import TokenTextSplitter
text_splitter = TokenTextSplitter(chunk_size=200, chunk_overlap=25)

for k,v in text_dict.items():
    text_chunks = text_splitter.split_text(v)
    for i, tc in enumerate(text_chunks):
        with open(f'./data/week_1/week_1_{k}_{i}.txt', 'w') as f:
            f.write(tc)

In [80]:
from langchain.document_loaders import DirectoryLoader

loader = DirectoryLoader('./data/week_1', glob="*.txt")
docs = loader.load()

In [81]:
db = FAISS.from_documents(docs, model_norm)

In [82]:
db.similarity_search("What is the goal of symptom investigation?")

[Document(page_content="1.1 Symptom InvestigationEffects00:00:00[MUSIC] 00:00:08[BLANK_AUDIO] 00:00:10Hi and welcome to lecture 1.1 symptom investigation. 00:00:17[BLANK_AUDIO] 00:00:24The objectives here for lecture 1.1 are to, let's see here, 00:00:32[BLANK_AUDIO] 00:00:35Summarize why a body diagram may provide useful information, describe the use of open and closed-ended questions as a component of symptom investigation. 00:00:47Describe how knowledge of potential pain location patterns associated with viscera, can be beneficial and how it can also be confounding. 00:00:56And finally, identify three questions you might ask a patient regarding the onset of their symptoms and describe the appropriate time frame over which to assess changes in their symptoms. 00:01:09[BL", metadata={'source': 'data/week_1/week_1_1.1_0.txt'}),
 Document(page_content="or burning. 00:04:18And visceral disorders could present with symptoms such as aching, squeezing, gnawing, burning or cramping. 00:04:26T

In [83]:
db.save_local("./dbs/week_1_db")

In [28]:
import collections
import re
from langchain.text_splitter import TokenTextSplitter
from langchain.document_loaders import DirectoryLoader

def index_one_pdf(path: str, splitter=TokenTextSplitter(chunk_size=200, chunk_overlap=25)):
    num = re.findall('\d+', path)[0]
    print(num)
    base_path = '../../Library/CloudStorage/Box-Box/DISC_AI Project/Transcripts Primary Care'
    read_pdf = pypdf.PdfReader(f'{base_path}/{path}')

    text_dict = collections.defaultdict(str)
    pages = read_pdf.pages
    for page in pages:
        page_text = page.extract_text()
        if page_text.startswith(f'{num}.'):
            curr = page_text[:3]
            text_dict[curr] += page_text
        else:
            text_dict[curr] += page_text

    os.makedirs(f'./data/week_{num}', exist_ok=True)

    for k,v in text_dict.items():
        text_chunks = splitter.split_text(v)
        for i, tc in enumerate(text_chunks):
            with open(f'./data/week_{num}/week_{num}_{k}_{i}.txt', 'w') as f:
                f.write(tc)

    loader = DirectoryLoader(f'./data/week_{num}', glob="*.txt")
    docs = loader.load()

    db = FAISS.from_documents(docs, model_norm)
    db.save_local(f"./dbs/week_{num}_db")

In [29]:
base_path = '../../Library/CloudStorage/Box-Box/DISC_AI Project/Transcripts Primary Care'
os.listdir(base_path)

['Week 8 Primary Care.pdf',
 'Week 3 Primary Care.pdf',
 'Week 7 Primary Care.pdf',
 'Weeks1_through_10.pdf',
 'Week 9 Primary Care.pdf',
 'Week 2 Primary Care.pdf',
 'Week 1 Primary Care.pdf',
 'Weeks1_through_5.pdf',
 'Week 5 Primary Care.pdf',
 'Week 4 Primary Care.pdf',
 'Week 10 Primary Care.pdf']

In [30]:
import re
pattern = "Week \d+ Primary Care.pdf"
files = sorted([f for f in os.listdir(base_path) if re.match(pattern, f)])
files

['Week 1 Primary Care.pdf',
 'Week 10 Primary Care.pdf',
 'Week 2 Primary Care.pdf',
 'Week 3 Primary Care.pdf',
 'Week 4 Primary Care.pdf',
 'Week 5 Primary Care.pdf',
 'Week 7 Primary Care.pdf',
 'Week 8 Primary Care.pdf',
 'Week 9 Primary Care.pdf']

In [37]:
for file in files:
    index_one_pdf(file)

1
10
2
3
4
5
7
8
9


╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <module>:2                                                                                    │
│                                                                                                  │
│   1 for file in files:                                                                           │
│ ❱ 2 │   index_one_pdf(file)                                                                      │
│   3                                                                                              │
│                                                                                                  │
│ in index_one_pdf:33                                                                              │
│                                                                                                  │
│   30 │   loader = DirectoryLoader(f'./data/week_{num}', glob="*.txt")                            │
│   31 │   docs = loader.load()                                                                    │
│   32 │                                                                                           │
│ ❱ 33 │   db = FAISS.from_documents(docs, model_norm)                                             │
│   34 │   db.save_local(f"./dbs/week_{num}_db")                                                   │
│   35                                                                                             │
│                                                                                                  │
│ /Users/pnadel01/miniconda3/envs/st_chat/lib/python3.10/site-packages/langchain/vectorstores/base │
│ .py:419 in from_documents                                                                        │
│                                                                                                  │
│   416 │   │   """Return VectorStore initialized from documents and embeddings."""                │
│   417 │   │   texts = [d.page_content for d in documents]                                        │
│   418 │   │   metadatas = [d.metadata for d in documents]                                        │
│ ❱ 419 │   │   return cls.from_texts(texts, embedding, metadatas=metadatas, **kwargs)             │
│   420 │                                                                                          │
│   421 │   @classmethod                                                                           │
│   422 │   async def afrom_documents(                                                             │
│                                                                                                  │
│ /Users/pnadel01/miniconda3/envs/st_chat/lib/python3.10/site-packages/langchain/vectorstores/fais │
│ s.py:603 in from_texts                                                                           │
│                                                                                                  │
│   600 │   │   │   │   embeddings = OpenAIEmbeddings()                                            │
│   601 │   │   │   │   faiss = FAISS.from_texts(texts, embeddings)                                │
│   602 │   │   """                                                                                │
│ ❱ 603 │   │   embeddings = embedding.embed_documents(texts)                                      │
│   604 │   │   return cls.__from(                                                                 │
│   605 │   │   │   texts,                                                                         │
│   606 │   │   │   embeddings,                                                                    │
│                                                                                                  │
│ /Users/pnadel01/miniconda3/envs/st_chat/lib/python3.10/site-packages/langchain/embeddings/huggin │
│ gface.py:252 in embed_documents                            

In [32]:
new_db = FAISS.load_local("./dbs/week_10_db/", model_norm)

In [33]:
new_db.similarity_search("What are common red flags?")

[Document(page_content="physicians asked about one-half to one-third of red flag identifying questions. 00:02:36In one study, only 27% of the red flag history questions were asked to patients who presented with low back pain. 00:02:43[BLANK_AUDIO] 00:02:50It's also important to keep in mind, though, that some findings that we call red flags are common. 00:02:57So some red flags are not an uncommon thing to stumble across. 00:03:02For example, of the 159 patient charts asking patients with low back pain whether they suffer from night or constant pain in this study, 71 of them noted a positive response. 00:03:15This doesn't mean that 71 of those 159 patients were immediately referred to their primary care provider. 00:03:22Instead, this finding is noted as important and is weighted along with the rest of the findings from the examination. 00:03:30So the specificity", metadata={'source': 'data/week_10/week_10_10._3.txt'}),
 Document(page_content="00:01:38So this table is taken from an art

In [35]:
compiled_files = sorted([f for f in os.listdir(base_path) if not re.match(pattern, f)])
compiled_files

['Weeks1_through_10.pdf', 'Weeks1_through_5.pdf']

In [39]:
base_path = '../../Library/CloudStorage/Box-Box/DISC_AI Project/Transcripts Primary Care'
pdf1 = pypdf.PdfReader(f'{base_path}/{compiled_files[0]}')
pdf2 = pypdf.PdfReader(f'{base_path}/{compiled_files[1]}')

In [42]:
pages = []
for page in pdf1.pages:
    pages.append(page)
for page in  pdf2.pages:
    pages.append(page)

In [43]:
pages

[{'/Contents': {'/Filter': '/FlateDecode'},
  '/CropBox': [0, 0, 612, 792],
  '/MediaBox': [0, 0, 612, 792],
  '/Parent': {'/Count': 6,
   '/Kids': [IndirectObject(1933, 0, 14436382800),
    IndirectObject(1, 0, 14436382800),
    IndirectObject(4, 0, 14436382800),
    IndirectObject(7, 0, 14436382800),
    IndirectObject(10, 0, 14436382800),
    IndirectObject(13, 0, 14436382800)],
   '/Parent': {'/Count': 26,
    '/Kids': [IndirectObject(1843, 0, 14436382800),
     IndirectObject(1844, 0, 14436382800),
     IndirectObject(1845, 0, 14436382800),
     IndirectObject(1846, 0, 14436382800),
     IndirectObject(1847, 0, 14436382800)],
    '/Parent': {'/Count': 166,
     '/Kids': [IndirectObject(1842, 0, 14436382800),
      IndirectObject(1848, 0, 14436382800),
      IndirectObject(1858, 0, 14436382800),
      IndirectObject(1864, 0, 14436382800),
      IndirectObject(1873, 0, 14436382800)],
     '/Parent': {'/Count': 391,
      '/Kids': [IndirectObject(1841, 0, 14436382800),
       Indirec

In [46]:
text_splitter = TokenTextSplitter(chunk_size=200, chunk_overlap=25)
text_dict = collections.defaultdict(str)
for page in pages:
    page_text = page.extract_text()
    if bool(re.match(r'^\d+', page_text)):
        curr = page_text[:3]
        text_dict[curr] += page_text
    else:
        text_dict[curr] += page_text

os.makedirs(f'./data/all_weeks', exist_ok=True)

for k,v in text_dict.items():
    text_chunks = text_splitter.split_text(v)
    for i, tc in enumerate(text_chunks):
        with open(f'./data/all_weeks/all_weeks_{k}_{i}.txt', 'w') as f:
            f.write(tc)

loader = DirectoryLoader(f'./data/all_weeks', glob="*.txt")
docs = loader.load()

db = FAISS.from_documents(docs, model_norm)
db.save_local(f"./dbs/all_weeks_db")

In [48]:
new_db = FAISS.load_local('./dbs/all_weeks_db/', model_norm)

In [49]:
new_db.similarity_search("What is resistance training?")

[Document(page_content="underlying life stressors may be important when treating things like tension headaches. 00:03:02In summary, the literature documents cases where patients presenting to physical therapy were found to have serious undiagnosed pathology upon therapist examination. 00:03:13And this underscores the need For the therapists to be familiar with red flags. 00:03:18Providers must understand the key features distinguishing musculoskeletal conditions suitable for conservative therapy. 00:03:25Versus those requiring urgent physician referral to ensure timely diagnosis and management. 00:03:32So we've covered a framework for generating a broad differential based on symptoms that the clinician should refine using history and examination to determine the need for escalation of care. 00:03:43The medical literature contains numerous case reports of patients presenting to physical therapy with common musculoskeletal complaints like arthrology of joint pain or dizziness. 00:03:53Wh